File clean up OANC

In [3]:
# Import necessary modules
import os

# Set your target directory here (e.g., '/home/user/my_folder')
target_dir = '/home/22ucc085/Crpto-net/OANC-GrAF/data'

# Validate the directory
if not os.path.isdir(target_dir):
    print(f"Directory does not exist: {target_dir}")
else:
    removed_files = []
    
    # Traverse the directory tree
    for root, dirs, files in os.walk(target_dir):
        for filename in files:
            # Check file extension (case-insensitive)
            if not filename.lower().endswith('.txt'):
                file_path = os.path.join(root, filename)
                try:
                    os.remove(file_path)
                    removed_files.append(file_path)
                except Exception as e:
                    print(f"Failed to remove {file_path}: {e}")
    
    # Report results
    print(f"\nRemoved {len(removed_files)} file(s):")
    for path in removed_files:
        print(path)



Removed 0 file(s):


Encrypt data using AES

In [14]:
import os
import binascii
from Crypto.Cipher import AES
from Crypto.Util.Padding import pad

def encrypt_aes_ecb_to_hex(plaintext: str, key: str) -> str:
    """
    Encrypts plaintext under AES-128 ECB, returns hex string.
    """
    # strip any trailing spaces/newlines so padding is consistent
    plaintext = plaintext.rstrip()
    cipher = AES.new(key.encode('utf-8'), AES.MODE_ECB)
    padded = pad(plaintext.encode('utf-8'), AES.block_size)
    encrypted = cipher.encrypt(padded)
    return encrypted.hex()

def hex_to_binary_string(hex_string: str) -> str | None:
    """
    Turns a hex string into a '010101...' string.
    """
    try:
        raw = binascii.unhexlify(hex_string)
        # each byte -> 8 bits
        return ''.join(f"{b:08b}" for b in raw)
    except binascii.Error as e:
        print(f"Error converting hex to binary: {e}")
        return None

def process_txt_files(input_folder: str, key: str, output_folder: str) -> None:
    """
    For each .txt in input_folder:
      - encrypt & write hex to output_folder/<basename>.txt.enc
      - convert that hex to binary and write to output_folder/<basename>_encrypted.txt
    """
    os.makedirs(output_folder, exist_ok=True)

    for root, _, files in os.walk(input_folder):
        for fname in files:
            if not fname.lower().endswith('.txt'):
                continue

            in_path = os.path.join(root, fname)
            with open(in_path, 'r', encoding='utf-8') as f:
                plaintext = f.read()

            # 1) Encrypt → hex
            hex_str = encrypt_aes_ecb_to_hex(plaintext, key)
            base = os.path.splitext(fname)[0]
            # hex_fname = f"{base}.txt.enc"
            # hex_out = os.path.join(output_folder, hex_fname)
            # with open(hex_out, 'w', encoding='utf-8') as f:
            #     f.write(hex_str)
            # print(f"Encrypted → {hex_fname}")

            # 2) Hex → binary
            bin_str = hex_to_binary_string(hex_str)
            if bin_str is None:
                print(f"Skipping binary conversion for {fname}")
                continue

            bin_fname = f"{base}_encrypted.txt"
            bin_out = os.path.join(output_folder, bin_fname)
            with open(bin_out, 'w', encoding='utf-8') as f:
                f.write(bin_str)
            print(f"Binary conversion → {bin_fname}")

if __name__ == "__main__":
    # 16‑byte key for AES‑128
    key = "raunakswamy12345"

    # change these to your actual paths
    input_folder  = "/home/22ucc085/Crpto-net/OANC-GrAF/data"
    output_folder = "/home/22ucc085/Crpto-net/AES"

    process_txt_files(input_folder, key, output_folder)


Binary conversion → AdamsElissa_encrypted.txt
Binary conversion → AdamsStephanie_encrypted.txt
Binary conversion → AdinolfiDavidandGail_encrypted.txt
Binary conversion → ArguetaBertila-ENG_encrypted.txt
Binary conversion → AverittShannon_encrypted.txt
Binary conversion → BlanchardTracy_encrypted.txt
Binary conversion → BorelRaymondHydeII_encrypted.txt
Binary conversion → BorelRaymondHydeIII_encrypted.txt
Binary conversion → BranchElbert_encrypted.txt
Binary conversion → CaseCullen_encrypted.txt
Binary conversion → CerdaAdam_encrypted.txt
Binary conversion → ChapmanDebbie_encrypted.txt
Binary conversion → CheezemBurt_encrypted.txt
Binary conversion → CombsJane_encrypted.txt
Binary conversion → CorderoRosalinda_encrypted.txt
Binary conversion → CottonGloria_encrypted.txt
Binary conversion → CoxJeremy_encrypted.txt
Binary conversion → DeLuciaBrian_encrypted.txt
Binary conversion → EmrichDavid_encrypted.txt
Binary conversion → EmrichMegan_encrypted.txt
Binary conversion → FarrowThomas_encr

Encrypt text using EL-Gmal

In [16]:
import random
import hashlib
import os

def number_to_binary_string(num):
    return bin(num)[2:]  # [2:] removes the '0b' prefix

def hex_to_binary_string(encrypted_blocks):
    binary = ''
    for c1, c2 in encrypted_blocks:
        binary += number_to_binary_string(c1).zfill(128)
        binary += number_to_binary_string(c2).zfill(128)
    return binary

def miller_rabin(n, k=5):
    """Miller-Rabin primality test"""
    if n == 2 or n == 3:
        return True
    if n < 2 or n % 2 == 0:
        return False

    # Write n-1 as 2^r * d
    r, d = 0, n - 1
    while d % 2 == 0:
        r += 1
        d //= 2

    # Witness loop
    for _ in range(k):
        a = random.randrange(2, n-1)
        x = pow(a, d, n)
        if x == 1 or x == n-1:
            continue
        for _ in range(r-1):
            x = (x * x) % n
            if x == n-1:
                break
        else:
            return False
    return True

def generate_key_128bit(key_string):
    key_bytes = key_string.encode('utf-8')
    key_hash = hashlib.sha256(key_bytes).hexdigest()

    # Start with a number close to 2^127 to ensure 128-bit size
    base = 2**127
    offset = int(key_hash[:32], 16) % (2**20)  # Use part of hash as offset
    starting_point = base + offset
    
    # Make sure it's odd
    if starting_point % 2 == 0:
        starting_point += 1

    # Find next prime
    while not miller_rabin(starting_point, k=10):
        starting_point += 2  # Skip even numbers

    p = starting_point
    
    # Find primitive root more efficiently
    g = find_primitive_root_efficient(p)
    
    # Generate private key
    x = int(key_hash[32:], 16) % (p - 1)
    if x == 0:
        x = 1

    h = pow(g, x, p)
    return (p, g, h)

def find_primitive_root_efficient(p):
    """More efficient primitive root finding"""
    if p == 2:
        return 1
        
    # For a prime p, we only need to test prime factors of p-1
    phi = p - 1
    factors = []
    
    # Find prime factors of phi
    n = phi
    for i in (2, 3, 5, 7, 11, 13, 17, 19, 23, 29, 31, 37, 41, 43, 47):
        if n % i == 0:
            factors.append(i)
            while n % i == 0:
                n //= i
    if n > 1:
        factors.append(n)
    
    # Test random numbers until we find a primitive root
    while True:
        g = random.randrange(2, p)
        if all(pow(g, phi // factor, p) != 1 for factor in factors):
            return g

def encrypt_text(message, public_key):
    p, g, h = public_key
    encrypted_blocks = []

    message_bytes = message.encode('utf-8')
    block_size = (p.bit_length() - 1) // 8

    for i in range(0, len(message_bytes), block_size):
        block = message_bytes[i:i + block_size]
        m = int.from_bytes(block, 'big')
        
        k = random.randint(1, p - 2)
        c1 = pow(g, k, p)
        s = pow(h, k, p)
        c2 = (m * s) % p
        
        encrypted_blocks.append((c1, c2))

    return encrypted_blocks

def encrypt_file(input_file_path, output_folder, public_key):
    try:
        with open(input_file_path, 'r', encoding='utf-8') as f:
            plaintext = f.read()

        encrypted_blocks = encrypt_text(plaintext, public_key)
        binary_text = hex_to_binary_string(encrypted_blocks)

        os.makedirs(output_folder, exist_ok=True)
        file_name = os.path.basename(input_file_path)
        encrypted_file_path = os.path.join(output_folder, f"{os.path.splitext(file_name)[0]}_encrypted.txt")

        with open(encrypted_file_path, 'w') as f:
            f.write(binary_text)

        print(f"File '{input_file_path}' encrypted and saved as binary in '{encrypted_file_path}'")
        print(f"Binary length: {len(binary_text)} bits")

    except Exception as e:
        print(f"Error encrypting file {input_file_path}: {str(e)}")

def encrypt_txt_files_in_folder(input_folder, output_folder, public_key):
    for root, dirs, files in os.walk(input_folder):
        for file in files:
            if file.endswith(".txt"):
                file_path = os.path.join(root, file)
                encrypt_file(file_path, output_folder, public_key)

def main():
    key = "raunakswamy12345"
    public_key = generate_key_128bit(key)
    
    input_folder = "/home/22ucc085/Crpto-net/OANC-GrAF/data"
    output_folder = "/home/22ucc085/Crpto-net/elgamal"
    encrypt_txt_files_in_folder(input_folder, output_folder, public_key)

if __name__ == "__main__":
    main()

File '/home/22ucc085/Crpto-net/OANC-GrAF/data/spoken/face-to-face/charlotte/AdamsElissa.txt' encrypted and saved as binary in '/home/22ucc085/Crpto-net/elgamal/AdamsElissa_encrypted.txt'
Binary length: 139008 bits
File '/home/22ucc085/Crpto-net/OANC-GrAF/data/spoken/face-to-face/charlotte/AdamsStephanie.txt' encrypted and saved as binary in '/home/22ucc085/Crpto-net/elgamal/AdamsStephanie_encrypted.txt'
Binary length: 116480 bits
File '/home/22ucc085/Crpto-net/OANC-GrAF/data/spoken/face-to-face/charlotte/AdinolfiDavidandGail.txt' encrypted and saved as binary in '/home/22ucc085/Crpto-net/elgamal/AdinolfiDavidandGail_encrypted.txt'
Binary length: 275456 bits
File '/home/22ucc085/Crpto-net/OANC-GrAF/data/spoken/face-to-face/charlotte/ArguetaBertila-ENG.txt' encrypted and saved as binary in '/home/22ucc085/Crpto-net/elgamal/ArguetaBertila-ENG_encrypted.txt'
Binary length: 388096 bits
File '/home/22ucc085/Crpto-net/OANC-GrAF/data/spoken/face-to-face/charlotte/AverittShannon.txt' encrypted 

Encrypt text using 3DES

In [20]:
import os
import binascii
from Crypto.Cipher import DES3
from Crypto.Util.Padding import pad

# ============ CONFIG ============

# 3DES key must be 16 or 24 bytes long
KEY = b'raunakswamy12345'  

# Folders
INPUT_FOLDER  = "/home/22ucc085/Crpto-net/OANC-GrAF/data"
OUTPUT_FOLDER = "/home/22ucc085/Crpto-net/3DES"

# ============ HELPERS ============

def hex_to_binary_string(hex_string: str) -> str:
    """
    Convert a hex string ("deadbeef…") into a single-line '0'/'1' string.
    """
    data = binascii.unhexlify(hex_string)
    # join each byte as 8 bits
    return ''.join(format(b, '08b') for b in data)


def encrypt_3des_ecb(plaintext: str, key: bytes) -> str:
    """
    Encrypts UTF-8 plaintext under 3DES-ECB with PKCS#7 padding,
    returns the ciphertext as a hex string.
    """
    cipher = DES3.new(key, DES3.MODE_ECB)
    padded = pad(plaintext.encode('utf-8'), DES3.block_size)
    ct = cipher.encrypt(padded)
    return binascii.hexlify(ct).decode('utf-8')


# ============ MAIN PROCESS ============

def encrypt_and_dump_binary(input_folder: str, output_folder: str):
    # ensure output folder exists
    os.makedirs(output_folder, exist_ok=True)

    for root, _, files in os.walk(input_folder):
        for fname in files:
            if not fname.lower().endswith('.txt'):
                continue

            in_path = os.path.join(root, fname)
            with open(in_path, 'r', encoding='utf-8') as f:
                plaintext = f.read()

            # 1) encrypt → hex
            hex_ct = encrypt_3des_ecb(plaintext, KEY)

            # 2) hex → one long binary string
            bin_str = hex_to_binary_string(hex_ct)

            # 3) write out as <basename>_encrypted.txt
            base = os.path.splitext(fname)[0]
            out_name = f"{base}_encrypted.txt"
            out_path = os.path.join(output_folder, out_name)

            with open(out_path, 'w', encoding='utf-8') as out:
                out.write(bin_str)

            print(f"Encrypted '{fname}' → '{out_name}' ({len(bin_str)} bits)")

if __name__ == "__main__":
    encrypt_and_dump_binary(INPUT_FOLDER, OUTPUT_FOLDER)


Encrypted 'AdamsElissa.txt' → 'AdamsElissa_encrypted.txt' (65088 bits)
Encrypted 'AdamsStephanie.txt' → 'AdamsStephanie_encrypted.txt' (54592 bits)
Encrypted 'AdinolfiDavidandGail.txt' → 'AdinolfiDavidandGail_encrypted.txt' (129088 bits)
Encrypted 'ArguetaBertila-ENG.txt' → 'ArguetaBertila-ENG_encrypted.txt' (181888 bits)
Encrypted 'AverittShannon.txt' → 'AverittShannon_encrypted.txt' (127232 bits)
Encrypted 'BlanchardTracy.txt' → 'BlanchardTracy_encrypted.txt' (65152 bits)
Encrypted 'BorelRaymondHydeII.txt' → 'BorelRaymondHydeII_encrypted.txt' (293824 bits)
Encrypted 'BorelRaymondHydeIII.txt' → 'BorelRaymondHydeIII_encrypted.txt' (98304 bits)
Encrypted 'BranchElbert.txt' → 'BranchElbert_encrypted.txt' (37696 bits)
Encrypted 'CaseCullen.txt' → 'CaseCullen_encrypted.txt' (62592 bits)
Encrypted 'CerdaAdam.txt' → 'CerdaAdam_encrypted.txt' (112640 bits)
Encrypted 'ChapmanDebbie.txt' → 'ChapmanDebbie_encrypted.txt' (578048 bits)
Encrypted 'CheezemBurt.txt' → 'CheezemBurt_encrypted.txt' (119

Encrypt text using Kasumi

In [23]:
import os
import binascii

# S-boxes for Kasumi algorithm (complete)
S7 = (
    54, 50, 62, 56, 22, 34, 94, 96, 38, 6, 63, 93, 2, 18, 123, 33,
    55, 113, 39, 114, 21, 67, 65, 12, 47, 73, 46, 27, 25, 111, 124, 81,
    53, 9, 121, 79, 52, 60, 58, 48, 101, 127, 40, 120, 104, 70, 71, 43,
    20, 122, 72, 61, 23, 109, 13, 100, 77, 1, 16, 7, 82, 10, 105, 98,
    117, 116, 76, 11, 89, 106, 0, 125, 118, 99, 86, 69, 30, 57, 126, 87,
    112, 51, 17, 5, 95, 14, 90, 84, 91, 8, 35, 103, 32, 97, 28, 66,
    102, 31, 26, 45, 75, 4, 85, 92, 37, 74, 80, 49, 68, 29, 115, 44,
    64, 107, 108, 24, 110, 83, 36, 78, 42, 19, 15, 41, 88, 119, 59, 3,
)

S9 = (
    167, 239, 161, 379, 391, 334, 9, 338, 38, 226, 48, 358, 452, 385, 90, 397,
    183, 253, 147, 331, 415, 340, 51, 362, 306, 500, 262, 82, 216, 159, 356, 177,
    175, 241, 489, 37, 206, 17, 0, 333, 44, 254, 378, 58, 143, 220, 81, 400,
    95, 3, 315, 245, 54, 235, 218, 405, 472, 264, 172, 494, 371, 290, 399, 76,
    165, 197, 395, 121, 257, 480, 423, 212, 240, 28, 462, 176, 406, 507, 288, 223,
    501, 407, 249, 265, 89, 186, 221, 428, 164, 74, 440, 196, 458, 421, 350, 163,
    232, 158, 134, 354, 13, 250, 491, 142, 191, 69, 193, 425, 152, 227, 366, 135,
    344, 300, 276, 242, 437, 320, 113, 278, 11, 243, 87, 317, 36, 93, 496, 27,
    487, 446, 482, 41, 68, 156, 457, 131, 326, 403, 339, 20, 39, 115, 442, 124,
    475, 384, 508, 53, 112, 170, 479, 151, 126, 169, 73, 268, 279, 321, 168, 364,
    363, 292, 46, 499, 393, 327, 324, 24, 456, 267, 157, 460, 488, 426, 309, 229,
    439, 506, 208, 271, 349, 401, 434, 236, 16, 209, 359, 52, 56, 120, 199, 277,
    465, 416, 252, 287, 246, 6, 83, 305, 420, 345, 153, 502, 65, 61, 244, 282,
    173, 222, 418, 67, 386, 368, 261, 101, 476, 291, 195, 430, 49, 79, 166, 330,
    280, 383, 373, 128, 382, 408, 155, 495, 367, 388, 274, 107, 459, 417, 62, 454,
    132, 225, 203, 316, 234, 14, 301, 91, 503, 286, 424, 211, 347, 307, 140, 374,
    35, 103, 125, 427, 19, 214, 453, 146, 498, 314, 444, 230, 256, 329, 198, 285,
    50, 116, 78, 410, 10, 205, 510, 171, 231, 45, 139, 467, 29, 86, 505, 32,
    72, 26, 342, 150, 313, 490, 431, 238, 411, 325, 149, 473, 40, 119, 174, 355,
    185, 233, 389, 71, 448, 273, 372, 55, 110, 178, 322, 12, 469, 392, 369, 190,
    1, 109, 375, 137, 181, 88, 75, 308, 260, 484, 98, 272, 370, 275, 412, 111,
    336, 318, 4, 504, 492, 259, 304, 77, 337, 435, 21, 357, 303, 332, 483, 18,
    47, 85, 25, 497, 474, 289, 100, 269, 296, 478, 270, 106, 31, 104, 433, 84,
    414, 486, 394, 96, 99, 154, 511, 148, 413, 361, 409, 255, 162, 215, 302, 201,
    266, 351, 343, 144, 441, 365, 108, 298, 251, 34, 182, 509, 138, 210, 335, 133,
    311, 352, 328, 141, 396, 346, 123, 319, 450, 281, 429, 228, 443, 481, 92, 404,
    485, 422, 248, 297, 23, 213, 130, 466, 22, 217, 283, 70, 294, 360, 419, 127,
    312, 377, 7, 468, 194, 2, 117, 295, 463, 258, 224, 447, 247, 187, 80, 398,
    284, 353, 105, 390, 299, 471, 470, 184, 57, 200, 348, 63, 204, 188, 33, 451,
    97, 30, 310, 219, 94, 160, 129, 493, 64, 179, 263, 102, 189, 207, 114, 402,
    438, 477, 387, 122, 192, 42, 381, 5, 145, 118, 180, 449, 293, 323, 136, 380,
    43, 66, 60, 455, 341, 445, 202, 432, 8, 237, 15, 376, 436, 464, 59, 461,
)

def _bitlen(x):
    return x.bit_length()

def _shift(x, s):
    return ((x << s) & 0xFFFF) | (x >> (16 - s))

def _mod(x):
    return ((x - 1) % 8) + 1

class Kasumi:
    def __init__(self):
        self.key_KL1 = [None]*9
        self.key_KL2 = [None]*9
        self.key_KO1 = [None]*9
        self.key_KO2 = [None]*9
        self.key_KO3 = [None]*9
        self.key_KI1 = [None]*9
        self.key_KI2 = [None]*9
        self.key_KI3 = [None]*9

    def set_key(self, master_key):
        key, key_prime = [None]*9, [None]*9
        master_key_prime = master_key ^ 0x0123456789ABCDEFFEDCBA9876543210
        for i in range(1,9):
            key[i] = (master_key >> (16*(8-i))) & 0xFFFF
            key_prime[i] = (master_key_prime >> (16*(8-i))) & 0xFFFF
        for i in range(1,9):
            self.key_KL1[i] = _shift(key[_mod(i)],1)
            self.key_KL2[i] = key_prime[_mod(i+2)]
            self.key_KO1[i] = _shift(key[_mod(i+1)],5)
            self.key_KO2[i] = _shift(key[_mod(i+5)],8)
            self.key_KO3[i] = _shift(key[_mod(i+6)],13)
            self.key_KI1[i] = key_prime[_mod(i+4)]
            self.key_KI2[i] = key_prime[_mod(i+3)]
            self.key_KI3[i] = key_prime[_mod(i+7)]

    def fun_FI(self, inp, rk):
        left, right = inp >> 7, inp & 0x7F
        rk1, rk2 = rk >> 9, rk & 0x1FF
        tmp_l, tmp_r = right, S9[left] ^ right
        left, right = tmp_r ^ rk2, S7[tmp_l] ^ (tmp_r & 0x7F) ^ rk1
        tmp_l, tmp_r = right, S9[left] ^ right
        left, right = S7[tmp_l] ^ (tmp_r & 0x7F), tmp_r
        return (left << 9) | right

    def fun_FO(self, inp, i):
        l, r = inp >> 16, inp & 0xFFFF
        o_l, o_r = r, self.fun_FI(l ^ self.key_KO1[i], self.key_KI1[i]) ^ r
        l2, r2 = o_r, self.fun_FI(o_l ^ self.key_KO2[i], self.key_KI2[i]) ^ o_r
        return (r2 << 16) | (self.fun_FI(l2 ^ self.key_KO3[i], self.key_KI3[i]) ^ r2)

    def fun_FL(self, inp, i):
        l, r = inp >> 16, inp & 0xFFFF
        r_out = r ^ _shift(l & self.key_KL1[i], 1)
        l_out = l ^ _shift(r_out | self.key_KL2[i], 1)
        return (l_out << 16) | r_out

    def fun_f(self, inp, i):
        return self.fun_FO(self.fun_FL(inp, i), i) if i % 2 else self.fun_FL(self.fun_FO(inp, i), i)

    def enc(self, block):
        l, r = block >> 32, block & 0xFFFFFFFF
        for i in range(1,9):
            l, r = r, l ^ self.fun_f(r, i)
        return (l << 32) | r

def encrypt_text(text, key_str):
    kas = Kasumi()
    kas.set_key(int.from_bytes(key_str.encode(), 'big'))
    data = text.encode('utf-8')
    pad_len = (8 - len(data) % 8) or 8
    data += bytes([pad_len])*pad_len
    cipher = b''
    for i in range(0, len(data), 8):
        block = int.from_bytes(data[i:i+8],'big')
        cipher += kas.enc(block).to_bytes(8,'big')
    return cipher.hex()

def hex_to_binary_string(hex_string):
    return ''.join(f'{b:08b}' for b in binascii.unhexlify(hex_string))

def encrypt_folder_to_binary(input_folder, output_folder, key_str):
    os.makedirs(output_folder, exist_ok=True)
    for root, _, files in os.walk(input_folder):
        for fname in files:
            if fname.endswith('.txt'):
                with open(os.path.join(root, fname),'r',encoding='utf-8') as f:
                    pt = f.read()
                hex_cipher = encrypt_text(pt, key_str)
                bin_str = hex_to_binary_string(hex_cipher)
                out_name = os.path.splitext(fname)[0] + '_encrypted.txt'
                with open(os.path.join(output_folder, out_name),'w',encoding='utf-8') as out_f:
                    out_f.write(bin_str)
                print(f"Encrypted {fname} -> {out_name}")

# Usage:
key = "raunakswamy12345"
input_folder = "/home/22ucc085/Crpto-net/OANC-GrAF/data"
output_folder = "/home/22ucc085/Crpto-net/kasumi"
encrypt_folder_to_binary(input_folder, output_folder, key)


Encrypted AdamsElissa.txt -> AdamsElissa_encrypted.txt
Encrypted AdamsStephanie.txt -> AdamsStephanie_encrypted.txt
Encrypted AdinolfiDavidandGail.txt -> AdinolfiDavidandGail_encrypted.txt
Encrypted ArguetaBertila-ENG.txt -> ArguetaBertila-ENG_encrypted.txt
Encrypted AverittShannon.txt -> AverittShannon_encrypted.txt
Encrypted BlanchardTracy.txt -> BlanchardTracy_encrypted.txt
Encrypted BorelRaymondHydeII.txt -> BorelRaymondHydeII_encrypted.txt
Encrypted BorelRaymondHydeIII.txt -> BorelRaymondHydeIII_encrypted.txt
Encrypted BranchElbert.txt -> BranchElbert_encrypted.txt
Encrypted CaseCullen.txt -> CaseCullen_encrypted.txt
Encrypted CerdaAdam.txt -> CerdaAdam_encrypted.txt
Encrypted ChapmanDebbie.txt -> ChapmanDebbie_encrypted.txt
Encrypted CheezemBurt.txt -> CheezemBurt_encrypted.txt
Encrypted CombsJane.txt -> CombsJane_encrypted.txt
Encrypted CorderoRosalinda.txt -> CorderoRosalinda_encrypted.txt
Encrypted CottonGloria.txt -> CottonGloria_encrypted.txt
Encrypted CoxJeremy.txt -> CoxJe

Encrypt text using RSA

In [24]:
from Crypto.PublicKey import RSA
from Crypto.Cipher import PKCS1_OAEP, AES
from Crypto.Random import get_random_bytes
import binascii
import os
from base64 import b64decode

# RSA Public Key (base64-encoded)
public_key_str = '''MFwwDQYJKoZIhvcNAQEBBQADSwAwSAJBANTs8qBHxpOTpyjiIMpUHUtCJckrAfOUNGIOJIsuRPj80rIU2DVBm3QqZulTR8n0HYCpLHbVxAb1o7RMATUISEMCAwEAAQ=='''
public_key = RSA.import_key(b64decode(public_key_str))

def aes_encrypt(plain_text):
    """Encrypt plain_text with AES-EAX; return key, nonce, ciphertext, tag."""
    aes_key = get_random_bytes(16)
    cipher = AES.new(aes_key, AES.MODE_EAX)
    ciphertext, tag = cipher.encrypt_and_digest(plain_text.encode('utf-8'))
    return aes_key, cipher.nonce, ciphertext, tag

def rsa_encrypt_key(aes_key):
    """Encrypt AES key with RSA-OAEP; return hex string."""
    cipher_rsa = PKCS1_OAEP.new(public_key)
    encrypted_key = cipher_rsa.encrypt(aes_key)
    return binascii.hexlify(encrypted_key).decode('utf-8')

def encrypt_large_text(plain_text):
    """AES-encrypt text, then RSA-encrypt AES key."""
    aes_key, nonce, ciphertext, tag = aes_encrypt(plain_text)
    encrypted_key = rsa_encrypt_key(aes_key)
    return encrypted_key, nonce, ciphertext, tag

def hex_to_binary_string(hex_str):
    """Convert hex string to binary string."""
    data = binascii.unhexlify(hex_str)
    return ''.join(f'{b:08b}' for b in data)

def encrypt_folder_to_binary(input_folder, output_folder):
    """Encrypt all .txt files in input_folder and save binary ciphertext."""
    os.makedirs(output_folder, exist_ok=True)
    for root, _, files in os.walk(input_folder):
        for fname in files:
            if fname.endswith('.txt'):
                path = os.path.join(root, fname)
                with open(path, 'r', encoding='utf-8') as f:
                    plaintext = f.read()
                encrypted_key, nonce, ciphertext, tag = encrypt_large_text(plaintext)
                # Convert ciphertext to binary string
                bin_cipher = hex_to_binary_string(ciphertext.hex())
                out_name = os.path.splitext(fname)[0] + '_encrypted.txt'
                out_path = os.path.join(output_folder, out_name)
                with open(out_path, 'w', encoding='utf-8') as out_f:
                    out_f.write(bin_cipher)
                print(f"Encrypted {fname} -> {out_name}")

# Usage:
input_folder = "/home/22ucc085/Crpto-net/OANC-GrAF/data"
output_folder = "/home/22ucc085/Crpto-net/RSA"
encrypt_folder_to_binary(input_folder, output_folder)


Encrypted AdamsElissa.txt -> AdamsElissa_encrypted.txt
Encrypted AdamsStephanie.txt -> AdamsStephanie_encrypted.txt
Encrypted AdinolfiDavidandGail.txt -> AdinolfiDavidandGail_encrypted.txt
Encrypted ArguetaBertila-ENG.txt -> ArguetaBertila-ENG_encrypted.txt
Encrypted AverittShannon.txt -> AverittShannon_encrypted.txt
Encrypted BlanchardTracy.txt -> BlanchardTracy_encrypted.txt
Encrypted BorelRaymondHydeII.txt -> BorelRaymondHydeII_encrypted.txt
Encrypted BorelRaymondHydeIII.txt -> BorelRaymondHydeIII_encrypted.txt
Encrypted BranchElbert.txt -> BranchElbert_encrypted.txt
Encrypted CaseCullen.txt -> CaseCullen_encrypted.txt
Encrypted CerdaAdam.txt -> CerdaAdam_encrypted.txt
Encrypted ChapmanDebbie.txt -> ChapmanDebbie_encrypted.txt
Encrypted CheezemBurt.txt -> CheezemBurt_encrypted.txt
Encrypted CombsJane.txt -> CombsJane_encrypted.txt
Encrypted CorderoRosalinda.txt -> CorderoRosalinda_encrypted.txt
Encrypted CottonGloria.txt -> CottonGloria_encrypted.txt
Encrypted CoxJeremy.txt -> CoxJe